In [1]:
import numpy as np
import numdifftools as nd
import matplotlib.pyplot as plt
import scipy.integrate as sp

In [9]:
# parameter values
V1 = -1.2
V2 = 18.
V3 = 2.
V4 = 30.
phi = 0.04
VK = -84.
VL = -60.
VCa = 120.
gK = 8.
gL = 2.
gCa = 4.4
Cm = 20.
tend = 1000
t = np.linspace(0,100,1000)
w0 = 0.014
initial = [[-10., w0],[-12., w0],[-14.,w0],[-16., w0],[-18.,w0],[-20.,w0]]

In [3]:
# definition of the functions m_inf, w_inf and tau
def m_inf(V, V1, V2):
    return 0.5*(1+np.tanh((V-V1)/V2))
def w_inf(V, V3, V4):
    return 0.5*(1+np.tanh((V-V3)/V4))
def tau(V, V3, V4):
    return 1/(np.cosh((V-V3)/V4))

In [7]:
# nullclines
def null1(V):
    return (-gCa*m_inf(V, V1, V2)*(V-VCa)-gL*(V-VL))/(gK*(V-VK))
def null2(V):
    return w_inf(V, V3, V4)

In [17]:
n1 = list()
n2 = list()
vrange = np.linspace(-70,70,280)
for i in vrange:
    n1.append(null1(i))
    n2.append(null2(i))
plt.plot(vrange, n1, label='n1')
plt.plot(vrange, n2, label='n2')
plt.xlabel('V')
plt.ylabel('n1, n2')
plt.legend(loc = 'center right')
plt.show()

In [4]:
def MLmodel((V, w), t, V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm):
    dV = (-gCa*m_inf(V, V2, V3)*(V-VCa)-gK*w*(V-VK)-gL*(V-VL))/Cm
    dw = phi *(w_inf(V, V3, V4)-w)/tau(V, V3, V4)
    return [dV, dw]

In [5]:
s = sp.odeint(MLmodel, (-50., 1.), t, args=(V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm))

In [42]:
plt.plot(t, s[:,0], label='V')
plt.plot(t, s[:,1], label='w')
plt.legend(loc='center right')
plt.xlabel('time')
plt.ylabel('V, w')
plt.show()

In [59]:
def steadystate((V, w), tol=1e-12):
    resList = list() 
    t = range(0,1000)
    resList.append([V, w])
    sol = sp.odeint(MLmodel, (V, w), t, args=(V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm)) 
    diff = np.linalg.norm([V, w], ord = 2) 
    i = 1 
    while i < len(t) and diff > tol: 
        L = sol[t[i]] 
        diff = np.linalg.norm(L-resList[-1], ord = 2)
        resList.append(L) 
        i = i + 1 
    return resList[-1]

ss = steadystate([-50.,1.])
print(ss[0], ss[1])

(-61.313374222385569, 0.014473000912913789)


In [16]:
# varying V0 in the initial conditions while keeping w0 at w*
for i in range(len(initial)):
    s = sp.odeint(MLmodel, initial[i], t, args=(V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm))
    plt.subplot(3,1,1)
    plt.title('V')
    plt.xlabel('time')
    plt.ylabel('V(t)')
    plt.plot(t,s[:,0], label=initial[i])
    plt.legend(loc='center right')
    plt.subplot(3,1,2)
    plt.title('w')
    plt.xlabel('time')
    plt.ylabel('w(t)')
    plt.plot(t,s[:,1], label=initial[i])
    plt.subplot(3,1,3)
    plt.title('Phase plane')
    plt.xlabel('V')
    plt.ylabel('w')
    plt.plot(s[:,0], s[:,1])
plt.tight_layout()
plt.show()